## Some general setup

In [13]:
# go wide screen
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [14]:
import os
import glob
import numpy as np
import os

In [15]:
class load_balanced_view_replace:
    
    def apply(self, func, *args):
        func(*args)
    
def func(a,b):
    print(a,b)
    
lv = load_balanced_view_replace()
lv.apply(func, 1, 2)

1 2


In [16]:
try:
    # have IPython.parallel?
    
    from ipyparallel import Client
    c = Client()
    lv = c.load_balanced_view()   # this object represents the engines (workers)
    print("Using IPython.parallel.")
except:
    class task:
        def __init__(self, result):
            self.result = result
            
        def get(self):
            return self.result
        
    # else, execute commands in sequence
    class load_balanced_view_replace:
    
        def apply(self, func, *args):
            return task( func(*args) )
    
    print("NOT using IPython.parallel. Did you forget to start the server?")
    lv = load_balanced_view_replace()

Using IPython.parallel.


In [17]:
prefix = ""
fields = ['gama09Efin','gama09Ffin','gama09Gfin','gama09Hfin']
fields = ['gama09Ffin']

## Apply spatial and spactral filtering to data cubes

In [21]:
def filter_cube(f, DRYRUN=True):
    import os
    h,t = os.path.split(f)
    cmd="python filter_cube.py --infile {} --outfile {} --sigma 1. --threshold 0.01".format(f,os.path.join(h,"sf" + t) )
    if DRYRUN:
        print(cmd)
        return -1, cmd
    else:
        return os.system( cmd ), cmd

In [22]:
# filter data cubes
ff = np.sort( glob.glob("../data/{}{}_???.fits.gz".format(prefix, field)) )

tasks = []
for f in ff:
    tasks.append(lv.apply(filter_cube, f))
result = [task.get() for task in tasks]  # blocks until all results are back

In [29]:
filter_cube('../data/gama09Ffin_069.fits.gz', DRYRUN=True)

python filter_cube.py --infile ../data/gama09Ffin_069.fits.gz --outfile ../data/sfgama09Ffin_069.fits.gz --sigma 1. --threshold 0.01


(-1,
 'python filter_cube.py --infile ../data/gama09Ffin_069.fits.gz --outfile ../data/sfgama09Ffin_069.fits.gz --sigma 1. --threshold 0.01')

## Build noise model cubes from data cubes

In [25]:
#build noise model
def noise_model(f, DRYRUN=True):
    import os
    h,t = os.path.split(f)
    cmd="python noise_model2.py --infile {} --outfile {}".format(f,os.path.join(h,"nc" + t) )
    if DRYRUN:
        print(cmd)
        return -1, cmd
    else:
        return os.system( cmd ), cmd

tasks = []
for f in ff:
    tasks.append(lv.apply(noise_model, f))
result = [task.get() for task in tasks]  # blocks until all results are back

for r in result:
    print(r)

(-1, 'python noise_model2.py --infile ../data/gama09Ffin_013.fits.gz --outfile ../data/ncgama09Ffin_013.fits.gz')
(-1, 'python noise_model2.py --infile ../data/gama09Ffin_014.fits.gz --outfile ../data/ncgama09Ffin_014.fits.gz')
(-1, 'python noise_model2.py --infile ../data/gama09Ffin_015.fits.gz --outfile ../data/ncgama09Ffin_015.fits.gz')
(-1, 'python noise_model2.py --infile ../data/gama09Ffin_016.fits.gz --outfile ../data/ncgama09Ffin_016.fits.gz')
(-1, 'python noise_model2.py --infile ../data/gama09Ffin_021.fits.gz --outfile ../data/ncgama09Ffin_021.fits.gz')
(-1, 'python noise_model2.py --infile ../data/gama09Ffin_022.fits.gz --outfile ../data/ncgama09Ffin_022.fits.gz')
(-1, 'python noise_model2.py --infile ../data/gama09Ffin_023.fits.gz --outfile ../data/ncgama09Ffin_023.fits.gz')
(-1, 'python noise_model2.py --infile ../data/gama09Ffin_024.fits.gz --outfile ../data/ncgama09Ffin_024.fits.gz')
(-1, 'python noise_model2.py --infile ../data/gama09Ffin_025.fits.gz --outfile ../data/n

## Apply spatial and spectral filtering to the noise model cubes

In [26]:
def filter_cube(f, DRYRUN=True):
    import os
    h,t = os.path.split(f)
    cmd="python filter_cube.py --infile {} --outfile {} --sigma 1. --threshold 0.01".format(f,os.path.join(h,"sf" + t) )
    if DRYRUN:
        print(cmd)
        return -1, cmd
    else:
        return os.system( cmd ), cmd

In [27]:
# filter noise cubes
ff = np.sort( glob.glob("../data/nc{}{}_???.fits.gz".format(prefix, field)) )

tasks = []
for f in ff:
    tasks.append(lv.apply(filter_cube, f))
result = [task.get() for task in tasks]  # blocks until all results are back

# don't need the unsmoothed noise cubes anymore
cmd="rm data/ncoutcube_{}_???.fits.gz".format(field)

In [28]:
filter_cube('../data/ncgama09Ffin_069.fits.gz', DRYRUN=True)

python filter_cube.py --infile ../data/ncgama09Ffin_069.fits.gz --outfile ../data/sfncgama09Ffin_069.fits.gz --sigma 1. --threshold 0.01


(-1,
 'python filter_cube.py --infile ../data/ncgama09Ffin_069.fits.gz --outfile ../data/sfncgama09Ffin_069.fits.gz --sigma 1. --threshold 0.01')

## Build polynomial noise models

In [14]:
# run detect and segmentation
def build_detect_noise_model(f, DRYRUN=True):
    import os
    detect_noise_model = f.replace(".fits.gz",".detect_noise_model")
    cmd = "python detection_noise_model.py -i {} -o {}".format(f,detect_noise_model)
    if DRYRUN:
        print(cmd)
        return -1, cmd
    else:
        return os.system( cmd ), cmd

ff = np.sort( glob.glob("../data/sf{}{}_???.fits.gz".format(prefix, field)) )


tasks = []
for f in ff:
    tasks.append(lv.apply(build_detect_noise_model, f))
result = [task.get() for task in tasks]  # blocks until all results are back

for r in result:
   print(r)

python detection_noise_model.py -i ../data/sfgama09Efin_013.fits.gz -o ../data/sfgama09Efin_013.detect_noise_model
python detection_noise_model.py -i ../data/sfgama09Efin_014.fits.gz -o ../data/sfgama09Efin_014.detect_noise_model
python detection_noise_model.py -i ../data/sfgama09Efin_015.fits.gz -o ../data/sfgama09Efin_015.detect_noise_model
python detection_noise_model.py -i ../data/sfgama09Efin_016.fits.gz -o ../data/sfgama09Efin_016.detect_noise_model
python detection_noise_model.py -i ../data/sfgama09Efin_021.fits.gz -o ../data/sfgama09Efin_021.detect_noise_model
python detection_noise_model.py -i ../data/sfgama09Efin_022.fits.gz -o ../data/sfgama09Efin_022.detect_noise_model
python detection_noise_model.py -i ../data/sfgama09Efin_023.fits.gz -o ../data/sfgama09Efin_023.detect_noise_model
python detection_noise_model.py -i ../data/sfgama09Efin_024.fits.gz -o ../data/sfgama09Efin_024.detect_noise_model
python detection_noise_model.py -i ../data/sfgama09Efin_025.fits.gz -o ../data/s

## Run Detections

The result will be a segmentation map.

In [33]:
sigma_detect_threshold = 5.
sigma_grow_threshold = 3.

def prepend(path, prefix):
    h,t = os.path.split(path)
    return os.path.join(h, prefix + t)

# run detect and segmentation
def cloud_finder3(f, field, sigma_detect_threshold, sigma_grow_threshold, DRYRUN=True):
    import os
    h,t = os.path.split(f)
    detect_noise_model = f.replace(".fits.gz",".detect_noise_model")
    
    cmd = "python cloud_finder3.py -i {} --sigma_detect_threshold {} --sigma_grow_threshold {} -b {} -o {} -n {}".\
        format(f,sigma_detect_threshold, sigma_grow_threshold,f.replace('.fits.gz','.badregs'),prepend(f.replace("sf",""), 'map'),detect_noise_model)
    if DRYRUN:
        print(cmd)
        return -1, cmd
    else:
        return os.system( cmd ), cmd
    
    return os.system( cmd )

ff = np.sort( glob.glob("../data/sf{}{}_???.fits.gz".format(prefix, field)) )
print("../data/sf{}{}_???.fits.gz".format(prefix, field))

tasks = []
for f in ff:
    tasks.append(lv.apply(cloud_finder3, f, field, sigma_detect_threshold, sigma_grow_threshold))
result = [task.get() for task in tasks]  # blocks until all results are back

for r in result:
    print(r)

../data/sfgama09Ffin_???.fits.gz


RemoteError: NameError(name 'prepend' is not defined)

In [34]:
#print("../data/sf{}{}_???.fits.gz".format(prefix, field))
cloud_finder3('../data/sfgama09Ffin_069.fits.gz', field, sigma_detect_threshold, sigma_grow_threshold, DRYRUN=True)

python cloud_finder3.py -i ../data/sfgama09Ffin_069.fits.gz --sigma_detect_threshold 5.0 --sigma_grow_threshold 3.0 -b ../data/sfgama09Ffin_069.badregs -o ../data/mapgama09Ffin_069.fits.gz -n ../data/sfgama09Ffin_069.detect_noise_model


(-1,
 'python cloud_finder3.py -i ../data/sfgama09Ffin_069.fits.gz --sigma_detect_threshold 5.0 --sigma_grow_threshold 3.0 -b ../data/sfgama09Ffin_069.badregs -o ../data/mapgama09Ffin_069.fits.gz -n ../data/sfgama09Ffin_069.detect_noise_model')

## Apply manual catalog if there is any (skip otherwise)

In [12]:
# add segmants for manually flagged 
def apply_manual_catalog(f, field, sigma_grow_threshold, DRYRUN=True):
    import os
    h,t = os.path.split(f)
    ifu = t.replace('.fits.gz','').split("_")[-1]
    fncatalog = "data/{}_{}.txt".format(field, ifu)
    detect_noise_model = f.replace(".fits.gz",".detect_noise_model")
    
    cmd = "python apply_manual_catalog.py -i {} -s {} -m {} -n {} -o {} -c {}".\
        format(f, sigma_grow_threshold, f.replace('sf2outcube','map'), \
               detect_noise_model, f.replace('sf2outcube','mmap'), fncatalog)
    if DRYRUN:
        print(cmd)
        return cmd
    else:
        return os.system( cmd ), cmd
    
    return os.system( cmd )

ff = np.sort( glob.glob("data/sf2outcube_{}_???.fits.gz".format(field)) )

sigma_grow_threshold = 2.0

tasks = []
for f in ff:
    tasks.append(lv.apply(apply_manual_catalog, f, field, sigma_grow_threshold))
result = [task.get() for task in tasks]  # blocks until all results are back

for r in result:
    print(r)

#python apply_manual_catalog.py -i data/sf2outcube_COSMOSC_021.fits.gz --sigma_grow_threshold 1.7  
#-m data/map_COSMOSC_021.fits.gz -n data/sf2outcube_COSMOSC_021.detect_noise_model -o data/mmap_COSMOSC_021.fits.gz -c data/COSMOSC_021.txt

## CCC Build the catalog from the segmentation map

In [35]:
ff = ["../data/sfgama09Ffin_069.fits.gz"] # datacube can't be read
ff = ["../data/sfgama09Ffin_078.fits.gz","../data/sfgama09Ffin_096.fits.gz"]
ff = ["../data/sfgama09Ffin_069.fits.gz"] # datacube can't be read


In [6]:
prefix = ""
fields = ['gama09Efin','gama09Ffin','gama09Gfin','gama09Hfin']
fields = ['gama09Gfin','gama09Hfin']
fields = ['gama09Efin','gama09Ffin']
ff = np.array([], dtype=str)
for field in fields:
    _ff = np.sort( glob.glob("../data/sf{}{}_???.fits.gz".format(prefix, field)) )
    ff = np.append(ff, _ff)

In [36]:
# build catalog
def build_catalog(f, DRYRUN=False):
    import os
    def prepend(path, prefix):
        h,t = os.path.split(path)
        return os.path.join(h, prefix + t)

    ifu = f[-11:-8]
    
    cmd = "python build_catalog.py -i {f} -m {m} -C 1e-17 -o {o} -n {n} --usemap --overwrite"\
        .format(f=f,m=prepend(f.replace("sf",""),"map"),o=f.replace(".fits",".cat").replace(".gz",""), n=f.replace(".fits.gz",".detect_noise_model") )
    
    if DRYRUN:
        return -1, cmd
    os.chdir("/data/hetdex/u/mxhf/mygama09/hetdex-deep")
    return os.system( cmd ), cmd

#ff = np.sort( glob.glob("../data/sf{}{}_???.fits.gz".format(prefix, field)) )

In [37]:
for f in ff[:1]:
    build_catalog(f, DRYRUN=False)

In [ ]:
tasks = []
for f in ff:
    tasks.append(lv.apply(build_catalog, f))
result = [task.get() for task in tasks]  # blocks until all results are back

for r in result:
    print(r)

## Filter for objects falling close to the edge of an IFU or close to nanpixels

In [49]:
#parallelized version

def filter_nans_and_edges(f, workdir, DEBUG = False):
    from astropy.table import Table, Column
    from matplotlib import pyplot as plt
    from astropy.io import fits
    import numpy as np
    from sklearn.neighbors import KDTree
    import numpy as np
    import matplotlib
    import os
    import copy
    

    os.chdir(workdir)

    print(f)
    #print("{} {}".format(field, ifu))


    tall = Table.read(f, format="ascii.ecsv")


    fcube = f.replace("sf", "").replace(".cat",".fits.gz")
    #fcube = "../data/{field}_{ifu}.fits.gz".format(field=field, ifu=ifu)
    fmap = f.replace("sf", "map").replace(".cat",".fits.gz")
    #fmap  = "../data/map{field}_{ifu}.fits.gz".format(field=field, ifu=ifu)


    tall.add_column(Column( [False]*len(tall), unit=""),name='touches_nan')
    tall.add_column(Column( [False]*len(tall), unit=""),name='touches_edge')

    if not os.path.exists(fcube):
        print("Cube {} not found, skipping.".format(fcube))
        return

    if not os.path.exists(fmap):
        print("Map {} not found, skipping.".format(fmap))
        return

    c    = fits.getdata(fcube)
    m    = fits.getdata(fmap)
    xx,yy = np.arange(c.shape[2]), np.arange(c.shape[1])
    XX,YY = np.meshgrid(xx,yy)

    ids = np.unique(tall["id"])
    #ids = [22]
    for id in ids:
        #print("Object {} {} {}".format(field, ifu, id))
        kk = (tall["id"] == id)
        r = tall[kk][0]
        # here we get a map of all the nan-pixel that exist
        # in the wavelength range of the object
        collnans = np.isnan( np.sum( c[ int(r["zmin"]):int(r["zmax"])], axis=0 ) )
        nanpixel = np.array([XX[collnans], YY[collnans]]).T
        # collapse map along z, maintaining all pixel that
        # belong to the current object ...
        ii = m == id
        collmap = np.sum(ii, axis=0) > 0
        # ... to get list of all X/Y coordinates belonging
        # to the object
        objpixel = np.array([XX[collmap], YY[collmap]]).T


        if (np.min( XX[collmap] ) < 2) or (np.min( YY[collmap] ) < 2) or \
            (np.max( XX[collmap] ) > XX.shape[1]-2) or (np.max( YY[collmap] ) > YY.shape[0]-2) or\
            (int(r["zmin"]) <=5) or (int(r["zmax"]) >= c.shape[0]-5):

                tall["touches_edge"][kk] = True
                if DEBUG:
                    print("Object {} touches edge".format(id))
                    fig = plt.figure()
                    plt.subplot(111)
                    plt.title("{} {} {}".format(field, ifu, id))
                    imcollnans = np.array(collnans, dtype=float)
                    imcollnans[~collnans] = np.nan
                    plt.imshow(imcollnans-1., origin='lower',vmin=0.,vmax=1.)
                    imcollmap = np.array(collmap, dtype=float)
                    imcollmap[~collmap] = np.nan
                    plt.imshow(imcollmap, origin='lower',vmin=0.,vmax=1.)

        ##  find neighbors in catalog nan for all pixels of the object
        X = objpixel
        Y = nanpixel
        C = np.vstack([X,Y])
        IX = np.array( [False] * len(X) + [True] * len(Y) )

        # build kdtree for combind list of objects
        tree = KDTree( C , leaf_size=2)              # doctest: +SKIP

        # find all neighbors of all objects within r = sqrt(2)
        #ind = tree.query_radius(X, r=1.414)
        ind = tree.query_radius(X, r=7.5)
        # determine which of these belong to the second catalog
        # checks if any of the current objects' pixels have any nan-pixel in their neighborhood
        no_nan_neighb = np.all( [ len(C[ ind[j][ IX[ ind[j] ] ]]) == 0 for j in range(len(X)) ] )
        tall["touches_nan"][kk] = ~no_nan_neighb

        if no_nan_neighb:
            #print("  Object {} has no nan-pixel in its neiborhood".format(id))
            pass
        else: 
            current_cmap = copy.copy( matplotlib.cm.get_cmap() )
            current_cmap.set_bad(color='None')
            if DEBUG:
                print("Object {} HAS nan-pixels in its neiborhood".format(id))
            if DEBUG:
                fig = plt.figure()
                plt.subplot(111)
                plt.title("{} {} {}".format(field, ifu, id))
                plt.text(XX.shape[1]/2., XX.shape[0]/9. ,"{} {} {}".format(field, ifu, id),ha='center')
                imcollnans = np.array(collnans, dtype=float)
                imcollnans[~collnans] = np.nan
                plt.imshow(imcollnans-1., origin='lower',vmin=0.,vmax=1.)
            
                imcollmap = np.array(collmap, dtype=float)
                imcollmap[~collmap] = np.nan
                plt.imshow(imcollmap, origin='lower',vmin=0.,vmax=1.)

                #plt.plot(X[:,0], X[:,1], 'r.') 
                for j in range(len(X))[:]:
                    nanpix = C[ ind[j][ IX[ ind[j] ] ]]
                    if len(nanpix) > 0.:
                        plt.plot(nanpix[:,0], nanpix[:,1], 'r.')
                            #print("{}:".format(j), nanpix)

        #
    print("{} objects touch nan pixels".format(sum( tall["touches_nan"] )) )  
    print("{} objects touch edge pixels".format(sum( tall["touches_edge"] )) )  
    tall.write(f.replace("sf","filtsf"), format="ascii.ecsv", overwrite=True)
    #1/0

In [50]:
prefix = ""
fields = ['gama09Gfin','gama09Hfin']
fields = ['gama09Efin','gama09Ffin']
ff = np.array([], dtype=str)
for field in fields:
    _ff = np.sort( glob.glob("../data/sf{}{}_???.cat".format(prefix, field)) )
    ff = np.append(ff, _ff)

In [51]:
if False:
    # testrun on one catalog
    workdir = "/data/hetdex/u/mxhf/mygama09/hetdex-deep"
    filter_nans_and_edges(ff[0], workdir, DEBUG = False)

In [52]:
workdir = "/data/hetdex/u/mxhf/mygama09/hetdex-deep"

tasks = []
for f in ff:
    tasks.append(lv.apply(filter_nans_and_edges, f, workdir))
result = [task.get() for task in tasks]  

for r in result:
    print(r)

None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None


# DDD Add continuum information

In [18]:
prefix = ""
fields = ['gama09Gfin','gama09Hfin', 'gama09Efin','gama09Ffin']
ff = np.array([], dtype=str)
for field in fields:
    _ff = np.sort( glob.glob("../data/sf{}{}_???.fits.gz".format(prefix, field)) )
    ff = np.append(ff, _ff)

In [19]:
def add_cnt_info(f, DRYRUN=False):
    import os
    workdir = "/data/hetdex/u/mxhf/mygama09/hetdex-deep"
    
    def prepend(path, prefix):
        h,t = os.path.split(path)
        return os.path.join(h, prefix + t)

    ifu = f[-11:-8]
    
    cmd="python cnt_level.py  -i {f} -m {m} -c {t} -o {o}"\
        .format(f=f,m=prepend(f.replace("sf",""),"map"),t=prepend(f.replace(".fits.gz",".cat"), 'filt'), o=prepend(f.replace(".fits.gz",".cat"), 'cntfilt') )
    
    if DRYRUN:
        return -1, cmd
    os.chdir(workdir)
    return os.system( cmd ), cmd

In [20]:
tasks = []
for f in ff:
    tasks.append(lv.apply(add_cnt_info, f ))
result = [task.get() for task in tasks]  

for r in result:
    print(r)

(0, 'python cnt_level.py  -i ../data/sfgama09Gfin_013.fits.gz -m ../data/mapgama09Gfin_013.fits.gz -c ../data/filtsfgama09Gfin_013.cat -o ../data/cntfiltsfgama09Gfin_013.cat')
(0, 'python cnt_level.py  -i ../data/sfgama09Gfin_014.fits.gz -m ../data/mapgama09Gfin_014.fits.gz -c ../data/filtsfgama09Gfin_014.cat -o ../data/cntfiltsfgama09Gfin_014.cat')
(0, 'python cnt_level.py  -i ../data/sfgama09Gfin_015.fits.gz -m ../data/mapgama09Gfin_015.fits.gz -c ../data/filtsfgama09Gfin_015.cat -o ../data/cntfiltsfgama09Gfin_015.cat')
(0, 'python cnt_level.py  -i ../data/sfgama09Gfin_016.fits.gz -m ../data/mapgama09Gfin_016.fits.gz -c ../data/filtsfgama09Gfin_016.cat -o ../data/cntfiltsfgama09Gfin_016.cat')
(0, 'python cnt_level.py  -i ../data/sfgama09Gfin_021.fits.gz -m ../data/mapgama09Gfin_021.fits.gz -c ../data/filtsfgama09Gfin_021.cat -o ../data/cntfiltsfgama09Gfin_021.cat')
(0, 'python cnt_level.py  -i ../data/sfgama09Gfin_022.fits.gz -m ../data/mapgama09Gfin_022.fits.gz -c ../data/filtsfgama

In [11]:
%pdb

Automatic pdb calling has been turned ON


## add manual info if available

In [224]:
# add segmants for manually flagged 
def add_manual_info(f, field, DRYRUN=True):
    import os
    h,t = os.path.split(f)
    ifu = t.replace('.fits.gz','').split("_")[-1]
    
    fncatalog = "data/{}_{}.txt".format(field, ifu)

    #python src/add_manual_info.py -m data/mmap_COSMOSC_021.fits.gz 
    # -c data/COSMOSC_021.txt -a data/msf2outcube_COSMOSC_021.cat
    
    cmd = "python src/add_manual_info.py -m {} -c {} -a {}".\
        format(f.replace('sf2outcube','mmap'), fncatalog, f.replace('.fits.gz','.cat').replace("sf2outcube","msf2outcube"))
    if DRYRUN:
        print(cmd)
        return cmd
    else:
        return os.system( cmd ), cmd
    
    return os.system( cmd )

ff = np.sort( glob.glob("data/sf2outcube_{}_???.fits.gz".format(field)) )

tasks = []
for f in ff:
    tasks.append(lv.apply(add_manual_info, f, field))
result = [task.get() for task in tasks]  # blocks until all results are back

for r in result:
    print(r)

python src/add_manual_info.py -m data/mmap_COSMOSC_021.fits.gz -c data/COSMOSC_021.txt -a data/msf2outcube_COSMOSC_021.cat
python src/add_manual_info.py -m data/mmap_COSMOSC_022.fits.gz -c data/COSMOSC_022.txt -a data/msf2outcube_COSMOSC_022.cat
python src/add_manual_info.py -m data/mmap_COSMOSC_023.fits.gz -c data/COSMOSC_023.txt -a data/msf2outcube_COSMOSC_023.cat
python src/add_manual_info.py -m data/mmap_COSMOSC_024.fits.gz -c data/COSMOSC_024.txt -a data/msf2outcube_COSMOSC_024.cat
python src/add_manual_info.py -m data/mmap_COSMOSC_025.fits.gz -c data/COSMOSC_025.txt -a data/msf2outcube_COSMOSC_025.cat
python src/add_manual_info.py -m data/mmap_COSMOSC_026.fits.gz -c data/COSMOSC_026.txt -a data/msf2outcube_COSMOSC_026.cat
python src/add_manual_info.py -m data/mmap_COSMOSC_027.fits.gz -c data/COSMOSC_027.txt -a data/msf2outcube_COSMOSC_027.cat
python src/add_manual_info.py -m data/mmap_COSMOSC_032.fits.gz -c data/COSMOSC_032.txt -a data/msf2outcube_COSMOSC_032.cat
python src/add_m

In [35]:
!pwd

/home/idies/workspace/Storage/mxhf/persistent/mygama09/hetdex-deep


## stack all catalogs

In [21]:
#combine (vstack) all tables from this field
from astropy.table import vstack, Column
from astropy.io import ascii

ttt = []
fields = ["gama09Efin", "gama09Ffin", "gama09Gfin", "gama09Hfin"]
for field in fields:
    ff = glob.glob("../data/cntfiltsf{field}_???.cat".format(field=field))
    #print(ff)
    tt = []
    for f in ff:
        ifu = f[-7:-4]
        print("{} {} {}".format(field, ifu, f))
        t = ascii.read(f, format="ecsv")
        t.add_column(Column([ifu]*len(t),name='ifu'),0)
        t.add_column(Column([field]*len(t),name='field'),0)
        print("    {}".format(len(t)))
        if len(t) == 0:
            continue
        tt.append(t)
        ttt.append(t)
        
    #1/0
        
    print("before vstack")
    tall = vstack(tt)
    print("after vstack")
    tall.write("../data/{field}.cat".format(field=field),format="ascii.ecsv")   

tall = vstack(ttt)
tall.write("../data/gama09EFGHfin_2.1.cat",format="ascii.ecsv")   


gama09Efin 105 ../data/cntfiltsfgama09Efin_105.cat
    306
gama09Efin 043 ../data/cntfiltsfgama09Efin_043.cat
    346
gama09Efin 083 ../data/cntfiltsfgama09Efin_083.cat
    278
gama09Efin 088 ../data/cntfiltsfgama09Efin_088.cat
    126
gama09Efin 036 ../data/cntfiltsfgama09Efin_036.cat
    223
gama09Efin 086 ../data/cntfiltsfgama09Efin_086.cat
    521
gama09Efin 103 ../data/cntfiltsfgama09Efin_103.cat
    61
gama09Efin 021 ../data/cntfiltsfgama09Efin_021.cat
    117
gama09Efin 089 ../data/cntfiltsfgama09Efin_089.cat
    1398
gama09Efin 046 ../data/cntfiltsfgama09Efin_046.cat
    119
gama09Efin 074 ../data/cntfiltsfgama09Efin_074.cat
    193
gama09Efin 063 ../data/cntfiltsfgama09Efin_063.cat
    93
gama09Efin 068 ../data/cntfiltsfgama09Efin_068.cat
    84
gama09Efin 094 ../data/cntfiltsfgama09Efin_094.cat
    344
gama09Efin 075 ../data/cntfiltsfgama09Efin_075.cat
    282
gama09Efin 081 ../data/cntfiltsfgama09Efin_081.cat
    21
gama09Efin 048 ../data/cntfiltsfgama09Efin_048.cat
    57
g

gama09Ffin 046 ../data/cntfiltsfgama09Ffin_046.cat
    180
gama09Ffin 022 ../data/cntfiltsfgama09Ffin_022.cat
    173
gama09Ffin 014 ../data/cntfiltsfgama09Ffin_014.cat
    232
gama09Ffin 052 ../data/cntfiltsfgama09Ffin_052.cat
    181
gama09Ffin 067 ../data/cntfiltsfgama09Ffin_067.cat
    298
gama09Ffin 078 ../data/cntfiltsfgama09Ffin_078.cat
    126
gama09Ffin 043 ../data/cntfiltsfgama09Ffin_043.cat
    191
gama09Ffin 076 ../data/cntfiltsfgama09Ffin_076.cat
    128
gama09Ffin 068 ../data/cntfiltsfgama09Ffin_068.cat
    358
gama09Ffin 075 ../data/cntfiltsfgama09Ffin_075.cat
    111
gama09Ffin 026 ../data/cntfiltsfgama09Ffin_026.cat
    353
gama09Ffin 103 ../data/cntfiltsfgama09Ffin_103.cat
    284
gama09Ffin 045 ../data/cntfiltsfgama09Ffin_045.cat
    108
gama09Ffin 083 ../data/cntfiltsfgama09Ffin_083.cat
    105
gama09Ffin 089 ../data/cntfiltsfgama09Ffin_089.cat
    3
gama09Ffin 015 ../data/cntfiltsfgama09Ffin_015.cat
    272
gama09Ffin 039 ../data/cntfiltsfgama09Ffin_039.cat
    99


gama09Gfin 030 ../data/cntfiltsfgama09Gfin_030.cat
    214
gama09Gfin 098 ../data/cntfiltsfgama09Gfin_098.cat
    252
gama09Gfin 047 ../data/cntfiltsfgama09Gfin_047.cat
    215
gama09Gfin 037 ../data/cntfiltsfgama09Gfin_037.cat
    251
gama09Gfin 091 ../data/cntfiltsfgama09Gfin_091.cat
    43
gama09Gfin 104 ../data/cntfiltsfgama09Gfin_104.cat
    171
gama09Gfin 028 ../data/cntfiltsfgama09Gfin_028.cat
    97
gama09Gfin 046 ../data/cntfiltsfgama09Gfin_046.cat
    125
gama09Gfin 086 ../data/cntfiltsfgama09Gfin_086.cat
    296
gama09Gfin 093 ../data/cntfiltsfgama09Gfin_093.cat
    114
gama09Gfin 058 ../data/cntfiltsfgama09Gfin_058.cat
    194
gama09Gfin 021 ../data/cntfiltsfgama09Gfin_021.cat
    101
gama09Gfin 024 ../data/cntfiltsfgama09Gfin_024.cat
    225
gama09Gfin 015 ../data/cntfiltsfgama09Gfin_015.cat
    268
gama09Gfin 084 ../data/cntfiltsfgama09Gfin_084.cat
    200
gama09Gfin 036 ../data/cntfiltsfgama09Gfin_036.cat
    199
gama09Gfin 033 ../data/cntfiltsfgama09Gfin_033.cat
    195

gama09Hfin 081 ../data/cntfiltsfgama09Hfin_081.cat
    231
gama09Hfin 073 ../data/cntfiltsfgama09Hfin_073.cat
    179
gama09Hfin 078 ../data/cntfiltsfgama09Hfin_078.cat
    37
gama09Hfin 103 ../data/cntfiltsfgama09Hfin_103.cat
    1254
gama09Hfin 094 ../data/cntfiltsfgama09Hfin_094.cat
    285
gama09Hfin 042 ../data/cntfiltsfgama09Hfin_042.cat
    210
gama09Hfin 076 ../data/cntfiltsfgama09Hfin_076.cat
    187
gama09Hfin 068 ../data/cntfiltsfgama09Hfin_068.cat
    76
gama09Hfin 074 ../data/cntfiltsfgama09Hfin_074.cat
    59
gama09Hfin 057 ../data/cntfiltsfgama09Hfin_057.cat
    93
gama09Hfin 091 ../data/cntfiltsfgama09Hfin_091.cat
    169
gama09Hfin 033 ../data/cntfiltsfgama09Hfin_033.cat
    232
gama09Hfin 034 ../data/cntfiltsfgama09Hfin_034.cat
    96
gama09Hfin 088 ../data/cntfiltsfgama09Hfin_088.cat
    83
gama09Hfin 026 ../data/cntfiltsfgama09Hfin_026.cat
    63
gama09Hfin 071 ../data/cntfiltsfgama09Hfin_071.cat
    210
gama09Hfin 015 ../data/cntfiltsfgama09Hfin_015.cat
    120
gam

## Augment with closeby HSC detections

In [22]:
# efficiently find neightbors in catalog Y for all objects in catalog X
from sklearn.neighbors import KDTree
import numpy as np

if False:
    rng = np.random.RandomState(0)
    X = rng.random_sample((10, 2))  # 10 points in 2 dimensions
    Y = rng.random_sample((10, 2))  # 10 points in 2 dimensions
    C = np.vstack([X,Y])
    IX = np.array( [False] * len(X) + [True] * len(Y) )

    # build kdtree for combind list of objects
    tree = KDTree( C , leaf_size=2)              # doctest: +SKIP

    # find all neighbors of first object within r = .3
    ind = tree.query_radius(X[:1], r=0.3)
    #print(ind[0])

    # determine wich of these belong to the second catalog
    # on only print these
    #print(ind[0][ IX[ ind[0] ] ] )


    # now do all

    # find all neighbors of all objects within r = .3
    ind = tree.query_radius(X, r=0.3)
    #print(ind[0])

    # determine which of these belong to the second catalog
    # on only print these
    for j in range(len(X)):
        # puh, this needs some explanation
        # j is the index to the current object in the X
        #  catalog
        # ind[j] contains indices to all neighbors in the combined catalog
        # IX is true only for objects in the combined catalog C that stem from Y
        # hence ind[j][ IX[ ind[j] are indices for all objects from Y
        # that are neighbors to the current object j
        # finally C[ ind[j][ IX[ ind[j] ] ]] are the coordinates
        # from the combined catalog, that are neighbors, but only showing
        # those that stem from Y.
        print("{}:".format(j), C[ ind[j][ IX[ ind[j] ] ]])
    

In [23]:
from astropy.table import Table, Column

thsc = Table.read("../hsc_small.ecsv",format="ascii.ecsv")

In [24]:
tall = Table.read("../data/gama09EFGHfin_2.1.cat",format="ascii.ecsv")

In [25]:
X = np.array([ tall['ra_com'], tall['dec_com'] ] ).T
Y = np.array([ thsc['ra'], thsc['dec'] ] ).T

In [26]:
# efficiently find neighbors in catalog Y for all objects in catalog X

from sklearn.neighbors import KDTree
import numpy as np
C = np.vstack([X,Y])
IX = np.array( [False] * len(X) + [True] * len(Y) )

# build kdtree for combind list of objects
tree = KDTree( C , leaf_size=2)              # doctest: +SKIP

In [27]:
# find all neighbors of all objects within r = .3
ind = tree.query_radius(X, r=2.5/3600.)
#print(ind[0])

In [28]:
tall.add_column( Column( [-1]*len(tall), format="{:d}", unit="") ,name='nmatchhsc') 

In [29]:
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit=""),name='match1_dist')
tall.add_column(Column( [np.nan]*len(tall), format="{:.6f}", unit="Deg"),name='match1_ra')
tall.add_column(Column( [np.nan]*len(tall), format="{:.6f}", unit="Deg"),name='match1_dec')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="mag"),name='match1_g_cmodel_mag')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="mag"),name='match1_g_cmodel_magsigma')
tall.add_column(Column( [np.nan]*len(tall), format="{:.3f}", unit=""),name='match1_photoz_best')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="A"),name='match1_EQW_lya')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="A"),name='match1_psfit_EQW_lya')

tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit=""),name='match2_dist')
tall.add_column(Column( [np.nan]*len(tall), format="{:.6f}", unit="Deg"),name='match2_ra')
tall.add_column(Column( [np.nan]*len(tall), format="{:.6f}", unit="Deg"),name='match2_dec')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="mag"),name='match2_g_cmodel_mag')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="mag"),name='match2_g_cmodel_magsigma')
tall.add_column(Column( [np.nan]*len(tall), format="{:.3f}", unit=""),name='match2_photoz_best')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="A"),name='match2_EQW_lya')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="A"),name='match2_psfit_EQW_lya')

tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit=""),name='match3_dist')
tall.add_column(Column( [np.nan]*len(tall), format="{:.6f}", unit="Deg"),name='match3_ra')
tall.add_column(Column( [np.nan]*len(tall), format="{:.6f}", unit="Deg"),name='match3_dec')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="mag"),name='match3_g_cmodel_mag')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="mag"),name='match3_g_cmodel_magsigma')
tall.add_column(Column( [np.nan]*len(tall), format="{:.3f}", unit=""),name='match3_photoz_best')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="A"),name='match3_EQW_lya')
tall.add_column(Column( [np.nan]*len(tall), format="{:.2f}", unit="A"),name='match3_psfit_EQW_lya')

In [30]:
def sphdist(ra1,dec1,ra2,dec2):
    d2 = ((ra1-ra2)*np.cos((dec1+dec2)/2.))**2. + (dec1-dec2)**2
    return np.sqrt(d2)

In [31]:
import astropy.units as u, astropy.constants as c, numpy as np

def EQW(Flya, magg):
    lam = 4670 * u.AA # sdss g-band effective wavelength
    dlam = 0.14 * lam # sdss g-band effective width    

    mg = (magg * u.ABmag)
    fg =  mg.to(u.erg/u.s/u.cm**2/u.AA , u.spectral_density(lam))

    Flya = Flya * u.erg/u.s/u.cm**2

    return float( ( Flya /fg ) /u.AA )

EQW(5e-17, 25.)

100.18046946369797

In [32]:
import astropy.units as u, astropy.constants as c, numpy as np

def EQW(Flya, magg):
    lam = 4670 * u.AA # sdss g-band effective wavelength
    dlam = 0.14 * lam # sdss g-band effective width    

    mg = (magg * u.ABmag)
    fg =  mg.to(u.erg/u.s/u.cm**2/u.AA , u.spectral_density(lam))
    print(fg)
    Flya = Flya * u.erg/u.s/u.cm**2

    return float( ( Flya /fg ) /u.AA )

EQW(5e-17, 25.)

4.990992782092952e-19 erg / (Angstrom cm2 s)


100.18046946369797

In [33]:
# determine which of these belong to the second catalog
# on only print these
for j in range(len(tall)):
    # puh, this needs some explanation
    # j is the index to the current object in the X
    #  catalog
    # ind[j] contains indices to all neighbors in the combined catalog
    # IX is true only for objects in the combined catalog C that stem from Y
    # hence ind[j][ IX[ ind[j] are indices for all objects from Y
    # that are neighbors to the current object j
    # finally C[ ind[j][ IX[ ind[j] ] ]] are the coordinates
    # from the combined catalog, that are neighbors, but only showing
    # those that stem from Y.
    #print("{}:".format(j), thsc[ ind[j][ IX[ ind[j] ] ] - len(X)  ][:3])
    
    matches = thsc[ ind[j][ IX[ ind[j] ] ] - len(X)  ]
    
    tall['nmatchhsc'][j] =  len(matches)
    
    # sort matches by distance
    dd = sphdist(matches['ra'],matches['dec'],tall['ra_com'][j],tall['dec_com'][j])*3600.
    ll = np.argsort(dd)
    matches = matches[ll]
    
    zlya = tall['wl_com'][j]/1216. - 1.
    
    if len(matches) > 0:
        tall['match1_dist'][j] = dd[0]
        tall['match1_ra'][j] = matches[0]['ra']
        tall['match1_dec'][j] = matches[0]['dec']
        tall['match1_g_cmodel_mag'][j] = matches[0]['g_cmodel_mag']
        tall['match1_g_cmodel_magsigma'][j] = matches[0]['g_cmodel_magsigma']
        tall['match1_photoz_best'][j] = matches[0]['photoz_best']
        tall['match1_EQW_lya'][j] = EQW(tall['flux'][j], matches[0]['g_cmodel_mag'])/(1. + zlya)
        tall['match1_psfit_EQW_lya'][j] = EQW(tall['psfit_flux'][j], matches[0]['g_cmodel_mag'])/(1. + zlya)
        
    if len(matches) > 1:
        tall['match2_dist'][j] = dd[1]
        tall['match2_ra'][j] = matches[1]['ra']
        tall['match2_dec'][j] = matches[1]['dec']
        tall['match2_g_cmodel_mag'][j] = matches[1]['g_cmodel_mag']
        tall['match2_g_cmodel_magsigma'][j] = matches[1]['g_cmodel_magsigma']
        tall['match2_photoz_best'][j] = matches[1]['photoz_best']
        tall['match2_EQW_lya'][j] = EQW(tall['flux'][j], matches[1]['g_cmodel_mag'])/(1. + zlya)
        tall['match2_psfit_EQW_lya'][j] = EQW(tall['psfit_flux'][j], matches[1]['g_cmodel_mag'])/(1. + zlya)

    if len(matches) > 2:
        tall['match3_dist'][j] = dd[2]
        tall['match3_ra'][j] = matches[2]['ra']
        tall['match3_dec'][j] = matches[2]['dec']
        tall['match3_g_cmodel_mag'][j] = matches[2]['g_cmodel_mag']
        tall['match3_g_cmodel_magsigma'][j] = matches[2]['g_cmodel_magsigma']
        tall['match3_photoz_best'][j] = matches[2]['photoz_best']
        tall['match3_EQW_lya'][j] = EQW(tall['flux'][j], matches[2]['g_cmodel_mag'])/(1. + zlya)
        tall['match3_psfit_EQW_lya'][j] = EQW(tall['psfit_flux'][j], matches[2]['g_cmodel_mag'])/(1. + zlya)

        
    #debug
    #if (tall["field"][j] == "gama09E") and (tall["ifu"][j] == "016") and( tall["id"][j] == 143):
    #    break
    


3.030208149050032e-17 erg / (Angstrom cm2 s)
3.030208149050032e-17 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
1.7567109234206987e-18 erg / (Angstrom cm2 s)
1.7567109234206987e-18 erg / (Angstrom cm2 s)
1.7519586908585114e-18 erg / (Angstrom cm2 s)
1.7519586908585114e-18 erg / (Angstrom cm2 s)
4.357540796598273e-19 erg / (Angstrom cm2 s)
4.357540796598273e-19 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
6.433155687429057e-19 erg / (Angstrom cm2 s)
6.433155687429057e-19 erg / (Angstrom cm2 s)
8.409275518758268e-20 erg / (Angstrom cm2 s)
8.409275518758268e-20 erg / (Angstrom cm2 s)
2.1844541910394703e-19 erg / (Angstrom cm2 s)
2.1844541910394703e-19 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
4.1435862361752363e-19 erg / (Angstrom cm2 s)
4.1435862361752363e-19 erg / (Angstrom cm2 s)
7.

/home/mxhf/.pyenv/versions/anaconda3-5.3.1/lib/python3.9/site-packages/astropy/table/column.py:1125: UserWarning: Warning: converting a masked element to nan.
  self.data[index] = value



4.348143032460243e-19 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
4.1435862361752363e-19 erg / (Angstrom cm2 s)
4.1435862361752363e-19 erg / (Angstrom cm2 s)
5.548556104656496e-19 erg / (Angstrom cm2 s)
5.548556104656496e-19 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
4.348143032460243e-19 erg / (Angstrom cm2 s)
4.348143032460243e-19 erg / (Angstrom cm2 s)
2.2219578785149312e-20 erg / (Angstrom cm2 s)
2.2219578785149312e-20 erg / (Angstrom cm2 s)
7.490142182020395e-18 erg / (Angstrom cm2 s)
7.490142182020395e-18 erg / (Angstrom cm2 s)
7.489865550225595e-18 erg / (Angstrom cm2 s)
7.489865550225595e-18 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
2.067488496393514e-19 erg / (Angstrom cm2 s)
4.348143032460243e-19 erg / (Angstrom cm2 s)
4.348143032460243e-19 erg / (Angstrom cm2 s)
1.1016502612942382e-18 erg / (Angstrom cm2 s)
1.10

/home/mxhf/.pyenv/versions/anaconda3-5.3.1/lib/python3.9/site-packages/astropy/units/quantity.py:479: RuntimeWarning: divide by zero encountered in true_divide
  result = super().__array_ufunc__(function, method, *arrays, **kwargs)


0.0 erg / (Angstrom cm2 s)
nan erg / (Angstrom cm2 s)
nan erg / (Angstrom cm2 s)
1.213220728357926e-19 erg / (Angstrom cm2 s)
1.213220728357926e-19 erg / (Angstrom cm2 s)
1.148444842647543e-19 erg / (Angstrom cm2 s)
1.148444842647543e-19 erg / (Angstrom cm2 s)
1.1706230244326946e-19 erg / (Angstrom cm2 s)
1.1706230244326946e-19 erg / (Angstrom cm2 s)
2.447156035993001e-17 erg / (Angstrom cm2 s)
2.447156035993001e-17 erg / (Angstrom cm2 s)
2.4588037216354453e-17 erg / (Angstrom cm2 s)
2.4588037216354453e-17 erg / (Angstrom cm2 s)
4.3340650144262394e-19 erg / (Angstrom cm2 s)
4.3340650144262394e-19 erg / (Angstrom cm2 s)
4.2513637173440143e-19 erg / (Angstrom cm2 s)
4.2513637173440143e-19 erg / (Angstrom cm2 s)
1.1561837517612501e-19 erg / (Angstrom cm2 s)
1.1561837517612501e-19 erg / (Angstrom cm2 s)
1.22688411018833e-19 erg / (Angstrom cm2 s)
1.22688411018833e-19 erg / (Angstrom cm2 s)
1.1590287844657562e-18 erg / (Angstrom cm2 s)
1.1590287844657562e-18 erg / (Angstrom cm2 s)
1.2814091

...

6.619413964146768e-21 erg / (Angstrom cm2 s)
6.619413964146768e-21 erg / (Angstrom cm2 s)
2.3198051155855223e-19 erg / (Angstrom cm2 s)
2.3198051155855223e-19 erg / (Angstrom cm2 s)
1.7147798903759796e-19 erg / (Angstrom cm2 s)
1.7147798903759796e-19 erg / (Angstrom cm2 s)
1.5816740224633865e-19 erg / (Angstrom cm2 s)
1.5816740224633865e-19 erg / (Angstrom cm2 s)
6.128593578467739e-20 erg / (Angstrom cm2 s)
6.128593578467739e-20 erg / (Angstrom cm2 s)
5.297437747093044e-19 erg / (Angstrom cm2 s)
5.297437747093044e-19 erg / (Angstrom cm2 s)
5.275956204104171e-19 erg / (Angstrom cm2 s)
5.275956204104171e-19 erg / (Angstrom cm2 s)
2.0944233054555826e-19 erg / (Angstrom cm2 s)
2.0944233054555826e-19 erg / (Angstrom cm2 s)
1.191440563212717e-19 erg / (Angstrom cm2 s)
1.191440563212717e-19 erg / (Angstrom cm2 s)
7.954028482174834e-20 erg / (Angstrom cm2 s)
7.954028482174834e-20 erg / (Angstrom cm2 s)
2.3910242555099667e-20 erg / (Angstrom cm2 s)
2.3910242555099667e-20 erg / (Angstrom cm2 s)


1.9081170921721234e-17 erg / (Angstrom cm2 s)
1.9081170921721234e-17 erg / (Angstrom cm2 s)
1.9093946518909094e-17 erg / (Angstrom cm2 s)
1.9093946518909094e-17 erg / (Angstrom cm2 s)
1.9093141089098242e-17 erg / (Angstrom cm2 s)
1.9093141089098242e-17 erg / (Angstrom cm2 s)
1.495325370313849e-19 erg / (Angstrom cm2 s)
1.495325370313849e-19 erg / (Angstrom cm2 s)
1.4901148466432635e-19 erg / (Angstrom cm2 s)
1.4901148466432635e-19 erg / (Angstrom cm2 s)
2.8037684328992486e-19 erg / (Angstrom cm2 s)
2.8037684328992486e-19 erg / (Angstrom cm2 s)
5.297437747093044e-19 erg / (Angstrom cm2 s)
5.297437747093044e-19 erg / (Angstrom cm2 s)
5.275956204104171e-19 erg / (Angstrom cm2 s)
5.275956204104171e-19 erg / (Angstrom cm2 s)
6.128593578467739e-20 erg / (Angstrom cm2 s)
6.128593578467739e-20 erg / (Angstrom cm2 s)
1.107347021384278e-19 erg / (Angstrom cm2 s)
1.107347021384278e-19 erg / (Angstrom cm2 s)
1.1024343630369102e-19 erg / (Angstrom cm2 s)
1.1024343630369102e-19 erg / (Angstrom cm2 s

7.456401785825388e-18 erg / (Angstrom cm2 s)
7.440516117708801e-18 erg / (Angstrom cm2 s)
7.440516117708801e-18 erg / (Angstrom cm2 s)
7.40801446689483e-18 erg / (Angstrom cm2 s)
7.40801446689483e-18 erg / (Angstrom cm2 s)
7.456401785825388e-18 erg / (Angstrom cm2 s)
7.456401785825388e-18 erg / (Angstrom cm2 s)
7.440516117708801e-18 erg / (Angstrom cm2 s)
7.440516117708801e-18 erg / (Angstrom cm2 s)
7.40801446689483e-18 erg / (Angstrom cm2 s)
7.40801446689483e-18 erg / (Angstrom cm2 s)
3.966193165206004e-19 erg / (Angstrom cm2 s)
3.966193165206004e-19 erg / (Angstrom cm2 s)
3.9858833244271026e-19 erg / (Angstrom cm2 s)
3.9858833244271026e-19 erg / (Angstrom cm2 s)
5.1112761066498306e-18 erg / (Angstrom cm2 s)
5.1112761066498306e-18 erg / (Angstrom cm2 s)
5.100799135750586e-18 erg / (Angstrom cm2 s)
5.100799135750586e-18 erg / (Angstrom cm2 s)
5.1009335005954245e-18 erg / (Angstrom cm2 s)
5.1009335005954245e-18 erg / (Angstrom cm2 s)
2.272144051911946e-18 erg / (Angstrom cm2 s)
2.272144

7.784440828268646e-20 erg / (Angstrom cm2 s)
1.2254000727963094e-19 erg / (Angstrom cm2 s)
1.2254000727963094e-19 erg / (Angstrom cm2 s)
1.4856451920436015e-18 erg / (Angstrom cm2 s)
1.4856451920436015e-18 erg / (Angstrom cm2 s)
1.485527793986431e-18 erg / (Angstrom cm2 s)
1.485527793986431e-18 erg / (Angstrom cm2 s)
7.456401785825388e-18 erg / (Angstrom cm2 s)
7.456401785825388e-18 erg / (Angstrom cm2 s)
7.440516117708801e-18 erg / (Angstrom cm2 s)
7.440516117708801e-18 erg / (Angstrom cm2 s)
7.40801446689483e-18 erg / (Angstrom cm2 s)
7.40801446689483e-18 erg / (Angstrom cm2 s)
nan erg / (Angstrom cm2 s)
nan erg / (Angstrom cm2 s)
nan erg / (Angstrom cm2 s)
nan erg / (Angstrom cm2 s)
nan erg / (Angstrom cm2 s)
nan erg / (Angstrom cm2 s)
2.1869192217500337e-19 erg / (Angstrom cm2 s)
2.1869192217500337e-19 erg / (Angstrom cm2 s)
2.241816709076725e-19 erg / (Angstrom cm2 s)
2.241816709076725e-19 erg / (Angstrom cm2 s)
1.960715318174127e-19 erg / (Angstrom cm2 s)
1.960715318174127e-19 er

2.7680128491877713e-19 erg / (Angstrom cm2 s)
2.7680128491877713e-19 erg / (Angstrom cm2 s)
nan erg / (Angstrom cm2 s)
nan erg / (Angstrom cm2 s)
2.1256260401596717e-19 erg / (Angstrom cm2 s)
2.1256260401596717e-19 erg / (Angstrom cm2 s)
2.7680128491877713e-19 erg / (Angstrom cm2 s)
2.7680128491877713e-19 erg / (Angstrom cm2 s)
2.7680128491877713e-19 erg / (Angstrom cm2 s)
2.7680128491877713e-19 erg / (Angstrom cm2 s)
1.0887291770079e-19 erg / (Angstrom cm2 s)
1.0887291770079e-19 erg / (Angstrom cm2 s)
1.0887291770079e-19 erg / (Angstrom cm2 s)
1.0887291770079e-19 erg / (Angstrom cm2 s)
5.091121970832169e-19 erg / (Angstrom cm2 s)
5.091121970832169e-19 erg / (Angstrom cm2 s)
0.0 erg / (Angstrom cm2 s)
0.0 erg / (Angstrom cm2 s)
1.1184654725247521e-18 erg / (Angstrom cm2 s)
1.1184654725247521e-18 erg / (Angstrom cm2 s)
2.7680128491877713e-19 erg / (Angstrom cm2 s)
2.7680128491877713e-19 erg / (Angstrom cm2 s)
2.7680128491877713e-19 erg / (Angstrom cm2 s)
2.7680128491877713e-19 erg / (An

In [35]:
tall.write("../data/augm_gama09EFGHfin_2.1.cat", format="ascii.ecsv", overwrite=True)

In [34]:
from astropy.io import ascii
tall = ascii.read("../data/augm_gama09EFGHfin_2.1.cat", format="ecsv")

FileNotFoundError: [Errno 2] No such file or directory: '../data/augm_gama09EFGHfin_2.1.cat'

In [19]:
kk  = tall["field"] == "gama09Gfin"
kk *= tall["ifu"] == "013"
kk *= tall["id"] == 2


In [21]:
tall[kk]

<Table length=1>
  field    ifu    id    N     counts        flux        ra_com      dec_com      ddec  ... match2_psfit_EQW_lya match3_dist match3_ra  match3_dec match3_g_cmodel_mag match3_g_cmodel_magsigma match3_photoz_best match3_EQW_lya match3_psfit_EQW_lya
                        px    counts   erg / (cm2 s)  RA[J2000]    Dec[J2000]   arcsec ...          A                          Deg        Deg             mag                   mag                                     A                 A          
  str10    str3 int64 int64  float64      float64      float64      float64    float64 ...       float64          float64    float64    float64         float64               float64               float64          float64           float64       
---------- ---- ----- ----- ---------- ------------- ------------ ------------ ------- ... -------------------- ----------- ---------- ---------- ------------------- ------------------------ ------------------ -------------- --------------------
gama09Gfin  013     2    68 1.7950e+00    3.5900e-17   130.184840     2.374480     0.7 ...                  nan        0.40 130.184942   2.374398               20.28                     0.00                nan           0.32                  nan

# OLD STUFF

In [11]:
# Old non parallelized version of nan/edge filter
from astropy.table import Table, Column
from matplotlib import pyplot as plt
from astropy.io import fits
import numpy as np
from sklearn.neighbors import KDTree
import numpy as np
import matplotlib
import os
%matplotlib inline


DEBUG = False
import copy


ff = np.sort( glob.glob("../data/sf*fin_???.cat") )

for f in ff:
        print(f)
        #print("{} {}".format(field, ifu))

        
        tall = Table.read(f, format="ascii.ecsv")
        

        fcube = f.replace("sf", "").replace(".cat",".fits.gz")
        #fcube = "../data/{field}_{ifu}.fits.gz".format(field=field, ifu=ifu)
        fmap = f.replace("sf", "map").replace(".cat",".fits.gz")
        #fmap  = "../data/map{field}_{ifu}.fits.gz".format(field=field, ifu=ifu)
        

        tall.add_column(Column( [False]*len(tall), unit=""),name='touches_nan')
        tall.add_column(Column( [False]*len(tall), unit=""),name='touches_edge')


        if not os.path.exists(fcube):
            print("Cube {} not found, skipping.".format(fcube))
            continue
            
        if not os.path.exists(fmap):
            print("Map {} not found, skipping.".format(fmap))
            continue

        c    = fits.getdata(fcube)
        m    = fits.getdata(fmap)
        xx,yy = np.arange(c.shape[2]), np.arange(c.shape[1])
        XX,YY = np.meshgrid(xx,yy)
        
        ids = np.unique(tall["id"])
        #ids = [22]
        for id in ids:
            #print("Object {} {} {}".format(field, ifu, id))
            kk = (tall["id"] == id)
            r = tall[kk][0]
            # here we get a map of all the nan-pixel that exist
            # in the wavelength range of the object
            collnans = np.isnan( np.sum( c[ int(r["zmin"]):int(r["zmax"])], axis=0 ) )
            nanpixel = np.array([XX[collnans], YY[collnans]]).T
            # collapse map along z, maintaining all pixel that
            # belong to the current object ...
            ii = m == id
            collmap = np.sum(ii, axis=0) > 0
            # ... to get list of all X/Y coordinates belonging
            # to the object
            objpixel = np.array([XX[collmap], YY[collmap]]).T
            

            if (np.min( XX[collmap] ) < 2) or (np.min( YY[collmap] ) < 2) or \
                (np.max( XX[collmap] ) > XX.shape[1]-2) or (np.max( YY[collmap] ) > YY.shape[0]-2) or\
                (int(r["zmin"]) <=5) or (int(r["zmax"]) >= c.shape[0]-5):

                    tall["touches_edge"][kk] = True
                    if DEBUG:
                        print("Object {} touches edge".format(id))
                        fig = plt.figure()
                        plt.subplot(111)
                        plt.title("{} {} {}".format(field, ifu, id))
                        imcollnans = np.array(collnans, dtype=float)
                        imcollnans[~collnans] = np.nan
                        plt.imshow(imcollnans-1., origin='lower',vmin=0.,vmax=1.)
                        imcollmap = np.array(collmap, dtype=float)
                        imcollmap[~collmap] = np.nan
                        plt.imshow(imcollmap, origin='lower',vmin=0.,vmax=1.)
            
            ##  find neighbors in catalog nan for all pixels of the object
            X = objpixel
            Y = nanpixel
            C = np.vstack([X,Y])
            IX = np.array( [False] * len(X) + [True] * len(Y) )

            # build kdtree for combind list of objects
            tree = KDTree( C , leaf_size=2)              # doctest: +SKIP

            # find all neighbors of all objects within r = sqrt(2)
            #ind = tree.query_radius(X, r=1.414)
            ind = tree.query_radius(X, r=7.5)
            # determine which of these belong to the second catalog
            # checks if any of the current objects' pixels have any nan-pixel in their neighborhood
            no_nan_neighb = np.all( [ len(C[ ind[j][ IX[ ind[j] ] ]]) == 0 for j in range(len(X)) ] )
            tall["touches_nan"][kk] = ~no_nan_neighb
            
            if no_nan_neighb:
                #print("  Object {} has no nan-pixel in its neiborhood".format(id))
                pass
            else: 
                current_cmap = copy.copy( matplotlib.cm.get_cmap() )
                current_cmap.set_bad(color='None')
                if DEBUG:
                    print("Object {} HAS nan-pixels in its neiborhood".format(id))
                if DEBUG:
                    fig = plt.figure()
                    plt.subplot(111)
                    plt.title("{} {} {}".format(field, ifu, id))
                    plt.text(XX.shape[1]/2., XX.shape[0]/9. ,"{} {} {}".format(field, ifu, id),ha='center')
                    imcollnans = np.array(collnans, dtype=float)
                    imcollnans[~collnans] = np.nan
                    plt.imshow(imcollnans-1., origin='lower',vmin=0.,vmax=1.)
                    imcollmap = np.array(collmap, dtype=float)
                    imcollmap[~collmap] = np.nan
                    plt.imshow(imcollmap, origin='lower',vmin=0.,vmax=1.)

                    #plt.plot(X[:,0], X[:,1], 'r.') 
                    for j in range(len(X))[:]:
                        nanpix = C[ ind[j][ IX[ ind[j] ] ]]
                        if len(nanpix) > 0.:
                            plt.plot(nanpix[:,0], nanpix[:,1], 'r.')
                                #print("{}:".format(j), nanpix)

            #
        print("{} objects touch nan pixels".format(sum( tall["touches_nan"] )) )  
        print("{} objects touch edge pixels".format(sum( tall["touches_edge"] )) )  
        tall.write(f.replace("sf","filtsf"), format="ascii.ecsv", overwrite=True)
        #1/0

../data/sfgama09Efin_013.cat
152 objects touch nan pixels
40 objects touch edge pixels
../data/sfgama09Efin_014.cat
143 objects touch nan pixels
17 objects touch edge pixels
../data/sfgama09Efin_015.cat
340 objects touch nan pixels
5 objects touch edge pixels
../data/sfgama09Efin_016.cat
248 objects touch nan pixels
16 objects touch edge pixels
../data/sfgama09Efin_021.cat
93 objects touch nan pixels
21 objects touch edge pixels
../data/sfgama09Efin_022.cat
156 objects touch nan pixels
29 objects touch edge pixels
../data/sfgama09Efin_023.cat
205 objects touch nan pixels
49 objects touch edge pixels
../data/sfgama09Efin_024.cat
256 objects touch nan pixels
0 objects touch edge pixels
../data/sfgama09Efin_025.cat
179 objects touch nan pixels
16 objects touch edge pixels
../data/sfgama09Efin_026.cat
119 objects touch nan pixels
0 objects touch edge pixels
../data/sfgama09Efin_027.cat


KeyboardInterrupt: 

## OLD Filter for objects falling close to the edge of an IFU or close to nanpixels

In [4]:
from astropy.table import Table, Column
from matplotlib import pyplot as plt
from astropy.io import fits
import numpy as np
from sklearn.neighbors import KDTree
from sklearn.neighbors import KDTree
import numpy as np
import matplotlib
import os
%matplotlib inline

In [5]:
tall = Table.read("../data/augm_gama09EFGHfin.cat", format="ascii.ecsv")

tall.add_column(Column( [False]*len(tall), unit=""),name='touches_nan')
tall.add_column(Column( [False]*len(tall), unit=""),name='touches_edge')


In [ ]:
DEBUG = False
import copy

fields = np.unique(tall['field'])
ifus   = np.unique(tall['ifu'])
#fields = ['gama09E']
#ifus = ["014"]

for field in fields:
    for ifu in ifus:
        print("{} {}".format(field, ifu))
        jj  = tall["field"] == field
        jj *= tall["ifu"]   == ifu
        
        fcube = "../data/{field}_{ifu}.fits.gz".format(field=field, ifu=ifu)
        fmap  = "../data/map{field}_{ifu}.fits.gz".format(field=field, ifu=ifu)
        
        if not os.path.exists(fcube):
            print("Cube {} not found, skipping.".format(fcube))
            continue
            
        if not os.path.exists(fmap):
            print("Map {} not found, skipping.".format(fmap))
            continue

        c    = fits.getdata(fcube)
        m    = fits.getdata(fmap)
        xx,yy = np.arange(c.shape[2]), np.arange(c.shape[1])
        XX,YY = np.meshgrid(xx,yy)
        
        ids = np.unique(tall["id"][jj])
        #ids = [22]
        for id in ids:
            #print("Object {} {} {}".format(field, ifu, id))
            kk = (tall["field"] == field) * (tall["ifu"]   == ifu) * (tall["id"] == id)
            r = tall[kk][0]
            # here we get a map of all the nan-pixel that exist
            # in the wavelength range of the object
            collnans = np.isnan( np.sum( c[ int(r["zmin"]):int(r["zmax"])], axis=0 ) )
            nanpixel = np.array([XX[collnans], YY[collnans]]).T
            # collapse map along z, maintaining all pixel that
            # belong to the current object ...
            ii = m == id
            collmap = np.sum(ii, axis=0) > 0
            # ... to get list of all X/Y coordinates belonging
            # to the object
            objpixel = np.array([XX[collmap], YY[collmap]]).T
            
            if DEBUG:
                print("foo")
                if (np.min( XX[collmap] ) < 2) or (np.min( YY[collmap] ) < 2) or \
                    (np.max( XX[collmap] ) > XX.shape[1]-2) or (np.max( YY[collmap] ) > YY.shape[0]-2) or\
                    (int(r["zmin"]) <=5) or (int(r["zmax"]) >= c.shape[0]-5):
                        
            tall["touches_edge"][kk] = True
            if DEBUG:
                print("  Object {} touches edge".format(id))
                fig = plt.figure()
                plt.subplot(111)
                plt.title("{} {} {}".format(field, ifu, id))
                imcollnans = np.array(collnans, dtype=float)
                imcollnans[~collnans] = np.nan
                plt.imshow(imcollnans-1., origin='lower',vmin=0.,vmax=1.)
                imcollmap = np.array(collmap, dtype=float)
                imcollmap[~collmap] = np.nan
                plt.imshow(imcollmap, origin='lower',vmin=0.,vmax=1.)
            
            ##  find neighbors in catalog nan for all pixels of the object
            X = objpixel
            Y = nanpixel
            C = np.vstack([X,Y])
            IX = np.array( [False] * len(X) + [True] * len(Y) )

            # build kdtree for combind list of objects
            tree = KDTree( C , leaf_size=2)              # doctest: +SKIP

            # find all neighbors of all objects within r = sqrt(2)
            #ind = tree.query_radius(X, r=1.414)
            ind = tree.query_radius(X, r=7.5)
            # determine which of these belong to the second catalog
            # checks if any of the current objects' pixels have any nan-pixel in their neighborhood
            no_nan_neighb = np.all( [ len(C[ ind[j][ IX[ ind[j] ] ]]) == 0 for j in range(len(X)) ] )
            tall["touches_nan"][kk] = ~no_nan_neighb
            
            if no_nan_neighb:
                #print("  Object {} has no nan-pixel in its neiborhood".format(id))
                pass
            else: 
                current_cmap = copy.copy( matplotlib.cm.get_cmap() )
                current_cmap.set_bad(color='None')
                if DEBUG:
                    print("Object {} HAS nan-pixels in its neiborhood".format(id))
                if DEBUG:
                    fig = plt.figure()
                    plt.subplot(111)
                    plt.title("{} {} {}".format(field, ifu, id))
                    plt.text(XX.shape[1]/2., XX.shape[0]/9. ,"{} {} {}".format(field, ifu, id),ha='center')
                    imcollnans = np.array(collnans, dtype=float)
                    imcollnans[~collnans] = np.nan
                    plt.imshow(imcollnans-1., origin='lower',vmin=0.,vmax=1.)
                    imcollmap = np.array(collmap, dtype=float)
                    imcollmap[~collmap] = np.nan
                    plt.imshow(imcollmap, origin='lower',vmin=0.,vmax=1.)

                    #plt.plot(X[:,0], X[:,1], 'r.') 
                    for j in range(len(X))[:]:
                        nanpix = C[ ind[j][ IX[ ind[j] ] ]]
                        if len(nanpix) > 0.:
                            plt.plot(nanpix[:,0], nanpix[:,1], 'r.')
                                #print("{}:".format(j), nanpix)

            #
                
tall.write("../data/filtaugm_gama09EFGHfin.cat", format="ascii.ecsv", overwrite=True)

gama09Efin 013
gama09Efin 014
gama09Efin 015
gama09Efin 016
gama09Efin 021
gama09Efin 022
gama09Efin 023
gama09Efin 024
gama09Efin 025
gama09Efin 026
gama09Efin 027
gama09Efin 028
gama09Efin 030
gama09Efin 031
gama09Efin 032
gama09Efin 033
gama09Efin 034
gama09Efin 035
gama09Efin 036
gama09Efin 037
gama09Efin 038
gama09Efin 039
gama09Efin 040
gama09Efin 041
gama09Efin 042
gama09Efin 043
gama09Efin 044
gama09Efin 045
gama09Efin 046
gama09Efin 047
gama09Efin 048
gama09Efin 049
gama09Efin 052
gama09Efin 053
gama09Efin 057
gama09Efin 058
gama09Efin 062
gama09Efin 063
gama09Efin 067
gama09Efin 068
gama09Efin 069
Cube ../data/gama09Efin_069.fits.gz not found, skipping.
gama09Efin 071
gama09Efin 072
gama09Efin 073
gama09Efin 074
gama09Efin 075
gama09Efin 076
gama09Efin 077
gama09Efin 078
gama09Efin 079
gama09Efin 081
gama09Efin 082
gama09Efin 083
gama09Efin 084
gama09Efin 085
gama09Efin 086
gama09Efin 087
gama09Efin 088
gama09Efin 089
gama09Efin 091
gama09Efin 092
gama09Efin 093
gama09Efin 09

In [9]:
os.path.exists("../data/mapgama09Hfin_095.fits.gz")

False

# OLD detection, not running on significances, DO NOT EXECUTE

detect_limits = {}

detect_limits['COSMOSA'] = { 'detect_threshold':0.35, 'grow_threshold':0.21}
detect_limits['COSMOSB'] = { 'detect_threshold':0.64, 'grow_threshold':0.39}
detect_limits['COSMOSC'] = { 'detect_threshold':0.64, 'grow_threshold':0.39}
detect_limits['COSMOSD'] = { 'detect_threshold':0.64, 'grow_threshold':0.39}

if False:
    # run detect and segmentation
    def cloud_finder2(f, field, detect_limits):
        import os
        h,t = os.path.split(f)
        dt, gt = detect_limits[field]['detect_threshold'], detect_limits[field]['grow_threshold']
        cmd = "python cloud_finder2.py -i {} --detect_threshold {} --grow_threshold {} -b {} -o {}".format(f,dt,gt,f.replace('.fits.gz','.badregs'),f.replace('sf2outcube','map'))
        return cmd
        #return os.system( cmd )

    ff = np.sort( glob.glob("data/sf2outcube_{}_???.fits.gz".format(field)) )

    tasks = []
    for f in ff:
        tasks.append(lv.apply(cloud_finder2, f, field, detect_limits))
    result = [task.get() for task in tasks]  # blocks until all results are back

    for r in result:
        print(r)